<h2>Chapter1: Gathering information of the list of Stations in Tokyo</h2>

In [1]:
#Importing libraries
from bs4 import BeautifulSoup
import requests
import pandas as pd
import numpy as np

In [2]:
#Importing libraries
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [3]:
#To Get all stations list in Tokyo
url_list = ['https://en.wikipedia.org/wiki/Category:Railway_stations_in_Tokyo', 
            'https://en.wikipedia.org/w/index.php?title=Category:Railway_stations_in_Tokyo&pagefrom=Kasai+Station#mw-pages', 
            'https://en.wikipedia.org/w/index.php?title=Category:Railway_stations_in_Tokyo&pagefrom=Okachimachi+Station#mw-pages', 
           'https://en.wikipedia.org/w/index.php?title=Category:Railway_stations_in_Tokyo&pagefrom=Tsukishima+Station#mw-pages']
def get_station_name_list(url_list):
    name_list = []
    for url in url_list:
        source = requests.get(url)
        html = BeautifulSoup(source.content, 'lxml')
        station_name_list = html.find('div', class_='mw-category')
        station_name = station_name_list.find_all('a')
        for a in station_name:
            name_list.append(a.string)
    return name_list

In [4]:
#Make the list by calling the function
name_list = get_station_name_list(url_list)

In [5]:
#Get latitude and longitude information through geopy

def get_geo_info(name_list):
    geolocator = Nominatim(user_agent="my-application", timeout=10)
    station_lst = []
    lati_lst = []
    lon_lst = []
    failed_lst = []
    for station_name in name_list:
        try:
            location = geolocator.geocode(station_name)
            latitude = location.latitude
            longitude = location.longitude
            station_lst.append(station_name)
            lati_lst.append(latitude)
            lon_lst.append(longitude)
        except:
            failed_lst.append(station_name)
        
    return station_lst, lati_lst, lon_lst, failed_lst

In [6]:
#Get the information by calling the function
station_lst, lati_lst, lon_lst, failed_lst = get_geo_info(name_list)

In [21]:
geolocator = Nominatim()
location = geolocator.geocode('Ukima-Funado Station')
latitude = location.latitude
longitude = location.longitude

/anaconda3/envs/UdacityDL/lib/python3.6/site-packages/ipykernel_launcher.py:1: DeprecationWarning: Using Nominatim with the default "geopy/1.18.1" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  """Entry point for launching an IPython kernel.


In [14]:
name_list

['Adachi-Odai Station',
 'Aihara Station',
 'Akabane Station',
 'Akabane-iwabuchi Station',
 'Akabanebashi Station',
 'Akado-shōgakkōmae Station',
 'Akasaka-mitsuke Station',
 'Akebonobashi Station',
 'Akigawa Station',
 'Akihabara Station',
 'Akishima Station',
 'Akitsu Station (Tokyo)',
 'Anamori-inari Station',
 'Aoi Station',
 'Aomi Station',
 'Aomono-yokochō Station',
 'Aoto Station',
 'Aoyama-itchōme Station',
 'Araiyakushi-mae Station',
 'Arakawa-itchūmae Station',
 'Arakawa-nanachōme Station',
 'Arakawa-nichōme Station',
 'Arakawa-shakomae Station',
 'Arakawa-yūenchimae Station',
 'Arakawakuyakushomae Station',
 'Ariake Station (Tokyo)',
 'Ariake-tennis-no-mori Station',
 'Asagaya Station',
 'Asakusa Station (Tokyo Metro, Toei, Tobu)',
 'Asakusa Station (Tsukuba Express)',
 'Asakusabashi Station',
 'Asukayama Station',
 'Awajichō Station',
 'Ayase Station',
 'Azabu-juban Station',
 'Bakuro-yokoyama Station',
 'Bakurochō Station',
 'Bubaigawara Station',
 'Chidorichō Station',
 

In [15]:
print(len(failed_lst))

171


In [16]:
print(failed_lst)

['Akabane-iwabuchi Station', 'Akishima Station', 'Akitsu Station (Tokyo)', 'Aomi Station', 'Arakawa-shakomae Station', 'Arakawa-yūenchimae Station', 'Arakawakuyakushomae Station', 'Asakusa Station (Tokyo Metro, Toei, Tobu)', 'Asakusa Station (Tsukuba Express)', 'Ayase Station', 'Bakurochō Station', 'Bubaigawara Station', 'Chidorichō Station', 'Ebaramachi Station', 'Fuchū Station (Tokyo)', 'Fuchūhommachi Station', 'Fuchūkeiba-seimommae Station', 'Fujimidai Station', 'Fussa Station', 'Gakushuinshita Station', 'Ginza-itchōme Station', 'Gokokuji Station', 'Hachiōji Station', 'Hachiōji-Minamino Station', 'Hagiyama Station', 'Hakusan Station (Tokyo)', 'Hamacho Station', 'Hamamatsuchō Station', 'Haneda Airport Domestic Terminal Station', 'Hanzōmon Station', 'Hatagaya Station', 'Hatsudai Station', 'Higashi-Azuma Station', 'Higashi-Kōenji Station', 'Higashi-Nagasaki Station', 'Higashi-Yamatoshi Station', 'Higashi-Mukōjima Station', 'Hikawadai Station', 'Hino Station (Tokyo)', 'Hitotsubashi-Gaku

In [7]:
#Make a dataframe by using the results
df = pd.DataFrame({'station':station_lst, 'latitude':lati_lst, 'longitude':lon_lst})

In [8]:
df.head()

station   latitude   longitude
0       Adachi-Odai Station  35.754678  139.770388
1            Aihara Station  35.606878  139.331680
2           Akabane Station  35.778139  139.720800
3  Akabane-iwabuchi Station  35.783147  139.720044
4      Akabanebashi Station  35.654970  139.743892

In [9]:
df.tail()

station   latitude   longitude
624        Yūrakuchō Station  35.675591  139.763305
625  Yushima Station (Tokyo)  35.708034  139.769806
626          Yūtenji Station  35.637575  139.691042
627        Zoshigaya Station  35.720260  139.714846
628          Zōshiki Station  35.550055  139.715197

In [38]:
df.to_csv('Stations_in_Tokyo.csv', )

In [3]:
df = pd.read_csv('Stations_in_Tokyo.csv')

In [4]:
df.head()

Unnamed: 0                   station   latitude   longitude
0           0       Adachi-Odai Station  35.754678  139.770388
1           1            Aihara Station  35.606878  139.331680
2           2           Akabane Station  35.778139  139.720800
3           3  Akabane-iwabuchi Station  35.783147  139.720044
4           4      Akabanebashi Station  35.654970  139.743893

In [5]:
df.drop(['Unnamed: 0'], axis=1, inplace=True)

<h2>Chapter2: Getting venue information of each station</h2>
**In this chapter, I will call FourSquare API and get venue information of each station.**

In [6]:
df.tail()

station   latitude   longitude
622        Yūrakuchō Station  35.675591  139.763305
623  Yushima Station (Tokyo)  35.708034  139.769806
624          Yūtenji Station  35.637575  139.691042
625        Zoshigaya Station  35.720260  139.714846
626          Zōshiki Station  35.550055  139.715197

In [10]:
#Make a map of Tokyo
address = 'Tokyo'
geolocator1 = Nominatim()
location = geolocator1.geocode(address)
latitude = location.latitude
longitude = location.longitude

map_tokyo = folium.Map(location=[latitude, longitude], zoom_start=10)


for lat, lng, station in zip(df['latitude'], df['longitude'], df['station']):
    label=station
    label=folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False
    ).add_to(map_tokyo)
    
map_tokyo

/anaconda3/envs/UdacityDL/lib/python3.6/site-packages/ipykernel_launcher.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.18.1" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  This is separate from the ipykernel package so we can avoid doing imports until


In [11]:
#Foursquare API Information

CLIENT_ID = 'KDCNWHDEJ4UYTSB3QHKSYWIS1JX0WZI50JRRQT540WXZSP2A' # your Foursquare ID
CLIENT_SECRET = 'DCA1AC0AGG020VE1TFXXCTNS4FEULN4R520AUM4ZE5MLFQMN' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('My credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

My credentails:
CLIENT_ID: KDCNWHDEJ4UYTSB3QHKSYWIS1JX0WZI50JRRQT540WXZSP2A
CLIENT_SECRET:DCA1AC0AGG020VE1TFXXCTNS4FEULN4R520AUM4ZE5MLFQMN


In [9]:
radius=500
LIMIT=100

url = url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)

results = requests.get(url).json()
results['response']
#['groups']
#[0]['items'
#[2]['venue']

{'groups': [{'items': [{'reasons': {'count': 0,
      'items': [{'reasonName': 'globalInteractionReason',
        'summary': 'This spot is popular',
        'type': 'general'}]},
     'referralId': 'e-0-4b5b9a56f964a520480a29e3-0',
     'venue': {'categories': [{'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/food_grocery_',
         'suffix': '.png'},
        'id': '52f2ab2ebcbc57f1066b8b46',
        'name': 'Supermarket',
        'pluralName': 'Supermarkets',
        'primary': True,
        'shortName': 'Supermarket'}],
      'id': '4b5b9a56f964a520480a29e3',
      'location': {'address': '仲六郷2-43-2',
       'cc': 'JP',
       'city': '東京',
       'country': '日本',
       'crossStreet': 'オーケージャンボサガンビルヂング',
       'distance': 58,
       'formattedAddress': ['仲六郷2-43-2 (オーケージャンボサガンビルヂング)',
        '大田区, 東京都',
        '144-0055',
        '日本'],
       'labeledLatLngs': [{'label': 'display',
         'lat': 35.55025080449875,
         'lng': 139.71579582786828}],
       

In [12]:
#function that extract the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list)==0:
        return None
    else:
        return categories_list[0]['name']

In [13]:
def getNearbyVenues(names, latitude, longitude, radius=500, LIMIT=100):
    venues_list=[]
    for name, lat, lng in zip(names, latitude, longitude):
        url='https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
        
        results = requests.get(url).json()['response']['groups'][0]['items']
        
        venues_list.append([(
            name,
            lat,
            lng,
            v['venue']['name'],
            v['venue']['location']['lat'],
            v['venue']['location']['lng'],
            v['venue']['categories'][0]['name']
                            ) for v in results])
        
        
    nearby_venues=pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns=['station',
                           'station Latitude',
                           'station Longitude',
                           'Venue',
                           'Venue Latitude',
                           'Venue Longitude',
                           'Venue Category'
        
    ]
    return (nearby_venues)

In [14]:
tokyo_venues = getNearbyVenues(df['station'], df['latitude'], df['longitude'])

In [22]:
df

station   latitude   longitude
0                              Adachi-Odai Station  35.754678  139.770388
1                                   Aihara Station  35.606878  139.331680
2                                  Akabane Station  35.778139  139.720800
3                         Akabane-iwabuchi Station  35.783147  139.720044
4                             Akabanebashi Station  35.654970  139.743893
5                        Akado-shōgakkōmae Station  35.742861  139.769042
6                          Akasaka-mitsuke Station  35.678216  139.735659
7                             Akebonobashi Station  35.692389  139.722861
8                                  Akigawa Station  35.728711  139.231226
9                                Akihabara Station  35.698565  139.773056
10                                Akishima Station  35.702480  139.350065
11                          Akitsu Station (Tokyo)  35.778504  139.496717
12                           Anamori-inari Station  35.550297  139.746746
13                                     Aoi Station  35.772109  139.820465
14                                    Aomi Station  35.624779  139.781202
15                          Aomono-yokochō Station  35.608874  139.743075
16                                    Aoto Station  35.745572  139.856123
17                          Aoyama-itchōme Station  35.671999  139.725183
18                         Araiyakushi-mae Station  35.715691  139.672657
19                        Arakawa-itchūmae Station  35.733717  139.788930
20                       Arakawa-nanachōme Station  35.741991  139.784140
21                         Arakawa-nichōme Station  35.738674  139.784665
22                        Arakawa-shakomae Station  35.750898  139.752787
23                          Ariake Station (Tokyo)  35.634560  139.793268
24                   Ariake-tennis-no-mori Station  35.640126  139.788861
25                                 Asagaya Station  35.704840  139.635472
26                            Asakusabashi Station  35.697337  139.786230
27                               Asukayama Station  35.750178  139.737400
28                                Awajichō Station  35.695129  139.767457
29                                   Ayase Station  35.761603  139.824035
30                             Azabu-juban Station  35.656496  139.736133
31                         Bakuro-yokoyama Station  35.692111  139.782778
32                               Bakurochō Station  35.693350  139.782453
33                             Bubaigawara Station  35.668477  139.468506
34                              Chidorichō Station  35.572899  139.691551
35                     Chikatetsu-Akatsuka Station  35.769913  139.644122
36                     Chikatetsu-Narimasu Station  35.776657  139.631302
37                       Chitose-Funabashi Station  35.647385  139.623820
38                      Chitose-karasuyama Station  35.668031  139.600869
39                           Chōfu Station (Tokyo)  35.598137  139.667320
40             Chūō-Daigaku-Meisei-Daigaku Station  35.641866  139.408762
41                           Daiba Station (Tokyo)  35.625902  139.771422
42                             Daikan-yama Station  35.648207  139.703262
43                          Daimon Station (Tokyo)  35.656794  139.754692
44                               Daishimae Station  35.778875  139.781463
45                              Daitabashi Station  35.671155  139.659604
46                            Den-en-chōfu Station  35.598137  139.667320
47                          Ebara-Nakanobu Station  35.609955  139.711953
48                           Ebisu Station (Tokyo)  35.646580  139.710215
49                                 Edogawa Station  35.737751  139.896051
50                            Edogawabashi Station  35.709522  139.733581
51                               Eifukuchō Station  35.676171  139.643853
52                                   Ekoda Station  35.737602  139.672750
53                               Etchūjima Stat

In [15]:
tokyo_venues.shape

(27016, 7)

In [66]:
tokyo_venues.to_csv('tokyo_venues_r500_l100.csv')

In [11]:
tokyo_venues = pd.read_csv('tokyo_venues_r500_l100.csv')

In [16]:
tokyo_venues.head()

station  station Latitude  station Longitude  \
0  Adachi-Odai Station         35.754678         139.770388   
1  Adachi-Odai Station         35.754678         139.770388   
2  Adachi-Odai Station         35.754678         139.770388   
3  Adachi-Odai Station         35.754678         139.770388   
4  Adachi-Odai Station         35.754678         139.770388   

                         Venue  Venue Latitude  Venue Longitude  \
0                オーケーストア 足立小台店       35.755243       139.768456   
1  MOS Burger (モスバーガー 島忠足立小台店)       35.755219       139.768133   
2             洋食レストラン 山惣(やまそう)       35.750813       139.768882   
3       K's Denki (ケーズデンキ 足立店)       35.754701       139.770530   
4                      扇大橋南交差点       35.755533       139.770271   

         Venue Category  
0           Supermarket  
1  Fast Food Restaurant  
2            Restaurant  
3     Electronics Store  
4          Intersection

In [13]:
tokyo_venues.groupby(['station']).count().reset_index().iloc[:,1]

0        8
1       16
2      100
3       58
4       58
5       24
6       85
7       72
8       11
9      100
10      10
11      57
12      41
13      18
14      40
15      48
16      38
17      70
18      24
19      40
20      44
21      21
22      31
23      63
24      11
25      58
26      56
27      27
28     100
29      65
30     100
31     100
32      89
33      52
34      19
35      39
36      61
37      46
38      72
39      34
40      12
41     100
42     100
43      74
44      18
45      38
46      34
47      51
48     100
49      18
50      49
51      28
52      49
53      29
54       6
55      19
56      31
57      26
58      21
59      48
60      28
61      15
62     100
63       5
64      50
65      44
66      19
67     100
68     100
69      27
70     100
71      25
72      28
73      45
74       9
75      28
76       8
77      21
78      13
79      40
80      40
81      40
82     100
83       8
84      28
85      51
86      57
87      58
88      79
89     100
90      22

<h2>Capter3: Data Processing and Clustering</h2>

In [17]:
#change the data into one hot encoding style
tokyo_onehot = pd.get_dummies(tokyo_venues['Venue Category'], prefix='', prefix_sep='')
tokyo_onehot['station'] = tokyo_venues['station']

fixed_columns=[tokyo_onehot.columns[-1]] + list(tokyo_onehot.columns[:-1])
tokyo_onehot = tokyo_onehot[fixed_columns]

tokyo_onehot.head()

station  ATM  Acai House  Accessories Store  Adult Boutique  \
0  Adachi-Odai Station    0           0                  0               0   
1  Adachi-Odai Station    0           0                  0               0   
2  Adachi-Odai Station    0           0                  0               0   
3  Adachi-Odai Station    0           0                  0               0   
4  Adachi-Odai Station    0           0                  0               0   

   Afghan Restaurant  African Restaurant  Airport  Airport Food Court  \
0                  0                   0        0                   0   
1                  0                   0        0                   0   
2                  0                   0        0                   0   
3                  0                   0        0                   0   
4                  0                   0        0                   0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Arcade  Argentinian Restaurant  Art Gallery  \
0             0         0       0                       0            0   
1             0         0       0                       0            0   
2             0         0       0                       0            0   
3             0         0       0                       0            0   
4             0         0       0                       0            0   

   Art Museum  Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0           0                    0                     0                 0   
1           0                    0                     0                 0   
2           0                    0                     0                 0   
3           0                    0                     0                 0   
4           0                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Auto Garage  \
0                   0           0                      0            0   
1                   0           0                      0            0   
2                   0           0                      0            0   
3                   0           0                      0            0   
4                   0           0                      0            0   

   Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bar  \
0              0          0           0           0       0    0   
1              0          0           0           0       0    0   
2              0          0           0           0       0    0   
3              0          0           0           0       0    0   
4              0          0           0           0       0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Bath House  Beach  \
0               0                 0                 0           0      0   
1               0                 0                 0           0      0   
2               0                 0                 0           0      0   
3               0                 0                 0           0      0   
4               0                 0                 0           0      0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Beijing Restaurant  \
0                0         0            0           0                   0   
1                0         0            0           0                   0   
2                0         0            0           0                   0   
3                0         0            0           0                   0   
4                0         0            

In [18]:
tokyo_grouped = tokyo_onehot.groupby(['station']).sum().reset_index()
tokyo_grouped.head()

station  ATM  Acai House  Accessories Store  \
0       Adachi-Odai Station    0           0                  0   
1            Aihara Station    0           0                  0   
2           Akabane Station    0           0                  0   
3  Akabane-iwabuchi Station    0           0                  0   
4      Akabanebashi Station    0           0                  0   

   Adult Boutique  Afghan Restaurant  African Restaurant  Airport  \
0               0                  0                   0        0   
1               0                  0                   0        0   
2               0                  0                   0        0   
3               0                  0                   0        0   
4               0                  0                   0        0   

   Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0                   0               0                0                 0   
1                   0               0                0                 0   
2                   0               0                0                 0   
3                   0               0                0                 0   
4                   0               0                0                 0   

   American Restaurant  Antique Shop  Aquarium  Arcade  \
0                    0             0         0       0   
1                    0             0         0       0   
2                    0             0         0       1   
3                    0             0         0       1   
4                    1             0         0       0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auditorium  \
0                     0                 0                   0           0   
1                     0                 0                   0           0   
2                     0                 0                   0           0   
3                     0                 0                   0           0   
4                     0                 0                   0           0   

   Australian Restaurant  Auto Garage  Auto Workshop  BBQ Joint  Baby Store  \
0                      0            0              0          0           0   
1                      0            0              0          0           0   
2                      0            0              0          3           0   
3                      0            0              0          2           0   
4                      0            0              0          0           0   

   Bagel Shop  Bakery  Bar  Baseball Field  Baseball Stadium  \
0           0       0    0               0                 0   
1           0       1    0               0                 0   
2           1       1    3               0                 0   
3           0       0    1               0                 0   
4           0       1    0               0                 0   

   Basketball Court  Bath House  Beach  Bed & Breakfast  Beer Bar  \
0                 0           0      0                0         0   
1                 0           0      0                0         0   
2                 0           0      0                0         0   
3                 0           1      0                0         0   
4                 0           0      0                0         0   

   Beer Garden  Beer Store  Beijing Restaurant  Belarusian Restaurant  \
0            0           0                   0                      0   
1            0           0                   0               

0      -1.000000
1      -1.000000
2      -1.000000
3      -1.000000
4      -1.000000
5      -1.000000
6      -1.000000
7      -1.000000
8      -1.000000
9      -1.000000
10     -1.000000
11     -1.000000
12     -1.000000
13     -1.000000
14     -1.000000
15     -1.000000
16     -1.000000
17     -1.000000
18     -1.000000
19     -1.000000
20     -1.000000
21     -1.000000
22     -1.000000
23     -1.000000
24     -1.000000
25     -1.000000
26     -1.000000
27     -1.000000
28     -1.000000
29     -1.000000
30     -1.000000
31     -1.000000
32     -1.000000
33     -1.000000
34     -1.000000
35     -1.000000
36     -1.000000
37     -1.000000
38     -1.000000
39     -1.000000
40     -1.000000
41     -1.000000
42     -1.000000
43     -1.000000
44     -1.000000
45     -1.000000
46     -1.000000
47     -1.000000
48     -1.000000
49     -1.000000
50     -1.000000
51     -1.000000
52     -1.000000
53     -1.000000
54     -1.000000
55     -1.000000
56     -1.000000
57     19.749364
58     -1.0000

In [16]:
#Normalize each column values based on each column value
for i in range(1, len(tokyo_grouped.columns)):
    mean = tokyo_grouped.iloc[:,i].mean()
    std = tokyo_grouped.iloc[:,i].std()
    tokyo_grouped.iloc[:,i] = (tokyo_grouped.iloc[:,i] - mean) / std
    
tokyo_grouped.head()

station       ATM  Acai House  Accessories Store  \
0       Adachi-Odai Station -0.210136   -0.040258          -0.102296   
1            Aihara Station -0.210136   -0.040258          -0.102296   
2           Akabane Station -0.210136   -0.040258          -0.102296   
3  Akabane-iwabuchi Station -0.210136   -0.040258          -0.102296   
4      Akabanebashi Station -0.210136   -0.040258          -0.102296   

   Adult Boutique  Afghan Restaurant  African Restaurant  Airport  \
0        -0.05698          -0.040258           -0.040258 -0.05698   
1        -0.05698          -0.040258           -0.040258 -0.05698   
2        -0.05698          -0.040258           -0.040258 -0.05698   
3        -0.05698          -0.040258           -0.040258 -0.05698   
4        -0.05698          -0.040258           -0.040258 -0.05698   

   Airport Food Court  Airport Lounge  Airport Service  American Restaurant  \
0            -0.05698       -0.069432        -0.054048            -0.171417   
1            -0.05698       -0.069432        -0.054048            -0.171417   
2            -0.05698       -0.069432        -0.054048            -0.171417   
3            -0.05698       -0.069432        -0.054048            -0.171417   
4            -0.05698       -0.069432        -0.054048             4.864970   

   Antique Shop  Aquarium    Arcade  Art Gallery  Art Museum  \
0     -0.040258  -0.05698 -0.227519    -0.189093   -0.196877   
1     -0.040258  -0.05698 -0.227519    -0.189093   -0.196877   
2     -0.040258  -0.05698 -0.227519    -0.189093   -0.196877   
3     -0.040258  -0.05698 -0.227519    -0.189093   -0.196877   
4     -0.040258  -0.05698 -0.227519    -0.189093   -0.196877   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auditorium  \
0            -0.171417         -0.270046           -0.146589   -0.040258   
1            -0.171417         -0.270046           -0.146589   -0.040258   
2            -0.171417         -0.270046           -0.146589   -0.040258   
3            -0.171417         -0.270046           -0.146589   -0.040258   
4            -0.171417         -0.270046           -0.146589   -0.040258   

   Australian Restaurant  Auto Garage  Auto Workshop  BBQ Joint  Baby Store  \
0              -0.080714    -0.069843      -0.069843  -0.554086   -0.069843   
1              -0.080714    -0.069843      -0.069843  -0.554086   -0.069843   
2              -0.080714    -0.069843      -0.069843   2.498334   -0.069843   
3              -0.080714    -0.069843      -0.069843  -0.554086   -0.069843   
4              -0.080714    -0.069843      -0.069843  -0.554086   -0.069843   

   Bagel Shop    Bakery      Bank       Bar  Baseball Field  Baseball Stadium  \
0   -0.069843 -0.511857 -0.069843 -0.366189       -0.116914         -0.085208   
1   -0.069843  1.059365 -0.069843 -0.366189       -0.116914         -0.085208   
2   -0.069843  1.059365 -0.069843  4.407162       -0.116914         -0.085208   
3   -0.069843 -0.511857 -0.069843 -0.366189       -0.116914         -0.085208   
4   -0.069843  2.630587 -0.069843 -0.366189       -0.116914         -0.085208   

   Bath House  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0   -0.260754        -0.322313 -0.254882    -0.102296    -0.05698   
1   -0.260754        -0.322313 -0.254882    -0.102296    -0.05698   
2   -0.260754        -0.322313 -0.254882    -0.102296    -0.05698   
3   -0.260754         1.589869 -0.254882    -0.102296    -0.05698   
4   -0.260754        -0.322313 -0.254882    -0.102296    -0.05698   

   Beijing Restaurant  Belarusian Restaurant  Betting Shop  Big Box Store  \
0           -0.040258              -0.040258     -0.040258      -0.040258   
1           -0.040258              -0.040258     -0.040258      -0.040258   
2           -0.040258              -0.040258     -0.040258      -0.040258   
3           -0.040258              -0.040258     -0.040258      -0.040258   
4           -0.040258              -0.040258     -0.040258      -0.040258   

   Bike Rental 

In [92]:
#Normalize each row based on each row value
for i in range (len(tokyo_grouped)):
    mean = tokyo_grouped.iloc[i, 1:].mean()
    std = tokyo_grouped.iloc[i, 1:].std()
    tokyo_grouped.iloc[i, 1:] = ( tokyo_grouped.iloc[i, 1:] - mean) / std

In [93]:
tokyo_grouped.head()

station       ATM  Acai House  Accessories Store  \
0       Adachi-Odai Station -0.124517   -0.124517          -0.124517   
1            Aihara Station -0.136614   -0.136614          -0.136614   
2           Akabane Station -0.167172   -0.167172          -0.167172   
3  Akabane-iwabuchi Station -0.189080   -0.189080          -0.189080   
4      Akabanebashi Station -0.212784   -0.212784          -0.212784   

   Adult Boutique  Afghan Restaurant  African Restaurant   Airport  \
0       -0.124517          -0.124517           -0.124517 -0.124517   
1       -0.136614          -0.136614           -0.136614 -0.136614   
2       -0.167172          -0.167172           -0.167172 -0.167172   
3       -0.189080          -0.189080           -0.189080 -0.189080   
4       -0.212784          -0.212784           -0.212784 -0.212784   

   Airport Food Court  Airport Lounge  Airport Service  American Restaurant  \
0           -0.124517       -0.124517        -0.124517            -0.124517   
1           -0.136614       -0.136614        -0.136614            -0.136614   
2           -0.167172       -0.167172        -0.167172            -0.167172   
3           -0.189080       -0.189080        -0.189080            -0.189080   
4           -0.212784       -0.212784        -0.212784             1.872495   

   Antique Shop  Aquarium    Arcade  Art Gallery  Art Museum  \
0     -0.124517 -0.124517 -0.124517    -0.124517   -0.124517   
1     -0.136614 -0.136614 -0.136614    -0.136614   -0.136614   
2     -0.167172 -0.167172 -0.167172    -0.167172   -0.167172   
3     -0.189080 -0.189080 -0.189080    -0.189080   -0.189080   
4     -0.212784 -0.212784 -0.212784    -0.212784   -0.212784   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auditorium  \
0            -0.124517         -0.124517           -0.124517   -0.124517   
1            -0.136614         -0.136614           -0.136614   -0.136614   
2            -0.167172         -0.167172           -0.167172   -0.167172   
3            -0.189080         -0.189080           -0.189080   -0.189080   
4            -0.212784         -0.212784           -0.212784   -0.212784   

   Australian Restaurant  Auto Garage  Auto Workshop  BBQ Joint  Baby Store  \
0              -0.124517    -0.124517      -0.124517  -0.124517   -0.124517   
1              -0.136614    -0.136614      -0.136614  -0.136614   -0.136614   
2              -0.167172    -0.167172      -0.167172   3.764724   -0.167172   
3              -0.189080    -0.189080      -0.189080  -0.189080   -0.189080   
4              -0.212784    -0.212784      -0.212784  -0.212784   -0.212784   

   Bagel Shop    Bakery      Bank       Bar  Baseball Field  Baseball Stadium  \
0   -0.124517 -0.124517 -0.124517 -0.124517       -0.124517         -0.124517   
1   -0.136614  4.326099 -0.136614 -0.136614       -0.136614         -0.136614   
2   -0.167172  1.143460 -0.167172  3.764724       -0.167172         -0.167172   
3   -0.189080 -0.189080 -0.189080 -0.189080       -0.189080         -0.189080   
4   -0.212784  3.957774 -0.212784 -0.212784       -0.212784         -0.212784   

   Bath House  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0   -0.124517        -0.124517 -0.124517    -0.124517   -0.124517   
1   -0.136614        -0.136614 -0.136614    -0.136614   -0.136614   
2   -0.167172        -0.167172 -0.167172    -0.167172   -0.167172   
3   -0.189080         3.033495 -0.189080    -0.189080   -0.189080   
4   -0.212784        -0.212784 -0.212784    -0.212784   -0.212784   

   Beijing Restaurant  Belarusian Restaurant  Betting Shop  Big Box Store  \
0           -0.124517              -0.124517     -0.124517      -0.124517   
1           -0.136614              -0.136614     -0.136614      -0.136614   
2           -0.167172              -0.167172     -0.167172      -0.167172   
3           -0.189080              -0.189080     -0.189080      -0.189080   
4           -0.212784              -0.212784     -0.212784      -0.212784   

   Bike R

In [19]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [20]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

columns = ['station', 'total number of venues']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))
        
neighbourhoods_venues_sorted = pd.DataFrame(columns=columns)
neighbourhoods_venues_sorted['station'] = tokyo_grouped['station']
neighbourhoods_venues_sorted['total number of venues'] = tokyo_venues.groupby(['station']).count().reset_index().iloc[:,1]

for ind in np.arange(tokyo_grouped.shape[0]):
    neighbourhoods_venues_sorted.iloc[ind, 2:] = return_most_common_venues(tokyo_grouped.iloc[ind, :], num_top_venues)
    
neighbourhoods_venues_sorted

station  total number of venues  \
0                              Adachi-Odai Station                       8   
1                                   Aihara Station                      16   
2                                  Akabane Station                     100   
3                         Akabane-iwabuchi Station                      61   
4                             Akabanebashi Station                      55   
5                        Akado-shōgakkōmae Station                      22   
6                          Akasaka-mitsuke Station                      86   
7                             Akebonobashi Station                      78   
8                                  Akigawa Station                      11   
9                                Akihabara Station                     100   
10                                Akishima Station                      12   
11                          Akitsu Station (Tokyo)                      58   
12                           Anamori-inari Station                      51   
13                                     Aoi Station                      19   
14                                    Aomi Station                      41   
15                          Aomono-yokochō Station                      49   
16                                    Aoto Station                      33   
17                          Aoyama-itchōme Station                      70   
18                         Araiyakushi-mae Station                      28   
19                        Arakawa-itchūmae Station                      36   
20                       Arakawa-nanachōme Station                      40   
21                         Arakawa-nichōme Station                      20   
22                        Arakawa-shakomae Station                      31   
23                          Ariake Station (Tokyo)                      81   
24                   Ariake-tennis-no-mori Station                      13   
25                                 Asagaya Station                      60   
26                            Asakusabashi Station                      49   
27                               Asukayama Station                      47   
28                                Awajichō Station                     100   
29                                   Ayase Station                      62   
30                             Azabu-juban Station                     100   
31                         Bakuro-yokoyama Station                     100   
32                               Bakurochō Station                      89   
33                             Bubaigawara Station                      53   
34                              Chidorichō Station                      19   
35                     Chikatetsu-Akatsuka Station                      40   
36                     Chikatetsu-Narimasu Station                      63   
37                       Chitose-Funabashi Station                      44   
38                      Chitose-karasuyama Station                      70   
39                           Chōfu Station (Tokyo)                      31   
40             Chūō-Daigaku-Meisei-Daigaku Station                      12   
41                           Daiba Station (Tokyo)                     100   
42                             Daikan-yama Station                     100   
43                          Daimon Station (Tokyo)                      79   
44                               Daishimae Station                      18   
45                              Daitabashi Station                      40   
46                            Den-en-chōfu Station                      31   
47                          Ebara-Nakanobu Station                      46   
48                           Ebisu Station (Tokyo)                     100   
49                                 Edogawa Station                      19   
50                            Edogawabashi Station               

In [35]:
#Cluster the data
kclusters = 5

tokyo_group_clustering = tokyo_grouped.drop('station', axis=1)

kmeans = KMeans(kclusters, random_state=0).fit(tokyo_group_clustering)

kmeans.labels_[:10]

array([3, 3, 0, 2, 1, 1, 4, 0, 3, 2], dtype=int32)

In [36]:
print(df.shape)
print(kmeans.labels_.shape)

(629, 3)
(620,)


In [37]:
#add cluster labels to the columns
neighbourhoods_venues_sorted['Cluster Label'] = kmeans.labels_
neighbourhoods_venues_sorted

station  total number of venues  \
0                              Adachi-Odai Station                       8   
1                                   Aihara Station                      16   
2                                  Akabane Station                     100   
3                         Akabane-iwabuchi Station                      61   
4                             Akabanebashi Station                      55   
5                        Akado-shōgakkōmae Station                      22   
6                          Akasaka-mitsuke Station                      86   
7                             Akebonobashi Station                      78   
8                                  Akigawa Station                      11   
9                                Akihabara Station                     100   
10                                Akishima Station                      12   
11                          Akitsu Station (Tokyo)                      58   
12                           Anamori-inari Station                      51   
13                                     Aoi Station                      19   
14                                    Aomi Station                      41   
15                          Aomono-yokochō Station                      49   
16                                    Aoto Station                      33   
17                          Aoyama-itchōme Station                      70   
18                         Araiyakushi-mae Station                      28   
19                        Arakawa-itchūmae Station                      36   
20                       Arakawa-nanachōme Station                      40   
21                         Arakawa-nichōme Station                      20   
22                        Arakawa-shakomae Station                      31   
23                          Ariake Station (Tokyo)                      81   
24                   Ariake-tennis-no-mori Station                      13   
25                                 Asagaya Station                      60   
26                            Asakusabashi Station                      49   
27                               Asukayama Station                      47   
28                                Awajichō Station                     100   
29                                   Ayase Station                      62   
30                             Azabu-juban Station                     100   
31                         Bakuro-yokoyama Station                     100   
32                               Bakurochō Station                      89   
33                             Bubaigawara Station                      53   
34                              Chidorichō Station                      19   
35                     Chikatetsu-Akatsuka Station                      40   
36                     Chikatetsu-Narimasu Station                      63   
37                       Chitose-Funabashi Station                      44   
38                      Chitose-karasuyama Station                      70   
39                           Chōfu Station (Tokyo)                      31   
40             Chūō-Daigaku-Meisei-Daigaku Station                      12   
41                           Daiba Station (Tokyo)                     100   
42                             Daikan-yama Station                     100   
43                          Daimon Station (Tokyo)                      79   
44                               Daishimae Station                      18   
45                              Daitabashi Station                      40   
46                            Den-en-chōfu Station                      31   
47                          Ebara-Nakanobu Station                      46   
48                           Ebisu Station (Tokyo)                     100   
49                                 Edogawa Station                      19   
50                            Edogawabashi Station               

In [38]:
#merge basic data with sorted data frame
tokyo_merged = df
tokyo_merged = tokyo_merged.merge(neighbourhoods_venues_sorted, on='station', how='left')
tokyo_merged

station   latitude   longitude  \
0                              Adachi-Odai Station  35.754678  139.770388   
1                                   Aihara Station  35.606878  139.331680   
2                                  Akabane Station  35.778139  139.720800   
3                         Akabane-iwabuchi Station  35.783147  139.720044   
4                             Akabanebashi Station  35.654970  139.743892   
5                        Akado-shōgakkōmae Station  35.742861  139.769042   
6                          Akasaka-mitsuke Station  35.678216  139.735659   
7                             Akebonobashi Station  35.692389  139.722861   
8                                  Akigawa Station  35.728711  139.231226   
9                                Akihabara Station  35.698565  139.773056   
10                                Akishima Station  35.702480  139.350065   
11                          Akitsu Station (Tokyo)  35.778504  139.496717   
12                           Anamori-inari Station  35.550297  139.746746   
13                                     Aoi Station  35.772109  139.820465   
14                                    Aomi Station  35.624779  139.781202   
15                          Aomono-yokochō Station  35.608874  139.743075   
16                                    Aoto Station  35.745572  139.856123   
17                          Aoyama-itchōme Station  35.671999  139.725183   
18                         Araiyakushi-mae Station  35.715691  139.672657   
19                        Arakawa-itchūmae Station  35.733717  139.788930   
20                       Arakawa-nanachōme Station  35.741991  139.784140   
21                         Arakawa-nichōme Station  35.738674  139.784665   
22                        Arakawa-shakomae Station  35.750898  139.752787   
23                          Ariake Station (Tokyo)  35.634560  139.793268   
24                   Ariake-tennis-no-mori Station  35.640126  139.788861   
25                                 Asagaya Station  35.704840  139.635472   
26                            Asakusabashi Station  35.697337  139.786230   
27                               Asukayama Station  35.752283  139.737056   
28                                Awajichō Station  35.695129  139.767457   
29                                   Ayase Station  35.761603  139.824035   
30                             Azabu-juban Station  35.656496  139.736133   
31                         Bakuro-yokoyama Station  35.692111  139.782778   
32                               Bakurochō Station  35.693350  139.782453   
33                             Bubaigawara Station  35.668477  139.468506   
34                              Chidorichō Station  35.572899  139.691551   
35                     Chikatetsu-Akatsuka Station  35.769913  139.644122   
36                     Chikatetsu-Narimasu Station  35.776657  139.631302   
37                       Chitose-Funabashi Station  35.647385  139.623820   
38                      Chitose-karasuyama Station  35.668031  139.600869   
39                           Chōfu Station (Tokyo)  35.598137  139.667319   
40             Chūō-Daigaku-Meisei-Daigaku Station  35.641866  139.408762   
41                           Daiba Station (Tokyo)  35.625902  139.771422   
42                             Daikan-yama Station  35.648207  139.703262   
43                          Daimon Station (Tokyo)  35.656794  139.754692   
44                               Daishimae Station  35.778875  139.781463   
45                              Daitabashi Station  35.671155  139.659604   
46                            Den-en-chōfu Station  35.598137  139.667319   
47                          Ebara-Nakanobu Station  35.609955  139.711953   
48                           Ebisu Station (Tokyo)  35.646580  139.710215   
49                                 Edogawa Station  35.737751  139.896051   
50                            Edogawabashi Station  35.709522  139.733581   
51                               Eifuku

In [39]:
#give label to columns that have NaN values
for i in range(len(tokyo_merged)):
    if np.isnan(tokyo_merged.iloc[i, -1]):
        tokyo_merged.iloc[i, -1] = kclusters

In [40]:
#change the datatype of Cluster Labels columns into int64
tokyo_merged['Cluster Label'] = tokyo_merged['Cluster Label'].astype(np.int64)
tokyo_merged

station   latitude   longitude  \
0                              Adachi-Odai Station  35.754678  139.770388   
1                                   Aihara Station  35.606878  139.331680   
2                                  Akabane Station  35.778139  139.720800   
3                         Akabane-iwabuchi Station  35.783147  139.720044   
4                             Akabanebashi Station  35.654970  139.743892   
5                        Akado-shōgakkōmae Station  35.742861  139.769042   
6                          Akasaka-mitsuke Station  35.678216  139.735659   
7                             Akebonobashi Station  35.692389  139.722861   
8                                  Akigawa Station  35.728711  139.231226   
9                                Akihabara Station  35.698565  139.773056   
10                                Akishima Station  35.702480  139.350065   
11                          Akitsu Station (Tokyo)  35.778504  139.496717   
12                           Anamori-inari Station  35.550297  139.746746   
13                                     Aoi Station  35.772109  139.820465   
14                                    Aomi Station  35.624779  139.781202   
15                          Aomono-yokochō Station  35.608874  139.743075   
16                                    Aoto Station  35.745572  139.856123   
17                          Aoyama-itchōme Station  35.671999  139.725183   
18                         Araiyakushi-mae Station  35.715691  139.672657   
19                        Arakawa-itchūmae Station  35.733717  139.788930   
20                       Arakawa-nanachōme Station  35.741991  139.784140   
21                         Arakawa-nichōme Station  35.738674  139.784665   
22                        Arakawa-shakomae Station  35.750898  139.752787   
23                          Ariake Station (Tokyo)  35.634560  139.793268   
24                   Ariake-tennis-no-mori Station  35.640126  139.788861   
25                                 Asagaya Station  35.704840  139.635472   
26                            Asakusabashi Station  35.697337  139.786230   
27                               Asukayama Station  35.752283  139.737056   
28                                Awajichō Station  35.695129  139.767457   
29                                   Ayase Station  35.761603  139.824035   
30                             Azabu-juban Station  35.656496  139.736133   
31                         Bakuro-yokoyama Station  35.692111  139.782778   
32                               Bakurochō Station  35.693350  139.782453   
33                             Bubaigawara Station  35.668477  139.468506   
34                              Chidorichō Station  35.572899  139.691551   
35                     Chikatetsu-Akatsuka Station  35.769913  139.644122   
36                     Chikatetsu-Narimasu Station  35.776657  139.631302   
37                       Chitose-Funabashi Station  35.647385  139.623820   
38                      Chitose-karasuyama Station  35.668031  139.600869   
39                           Chōfu Station (Tokyo)  35.598137  139.667319   
40             Chūō-Daigaku-Meisei-Daigaku Station  35.641866  139.408762   
41                           Daiba Station (Tokyo)  35.625902  139.771422   
42                             Daikan-yama Station  35.648207  139.703262   
43                          Daimon Station (Tokyo)  35.656794  139.754692   
44                               Daishimae Station  35.778875  139.781463   
45                              Daitabashi Station  35.671155  139.659604   
46                            Den-en-chōfu Station  35.598137  139.667319   
47                          Ebara-Nakanobu Station  35.609955  139.711953   
48                           Ebisu Station (Tokyo)  35.646580  139.710215   
49                                 Edogawa Station  35.737751  139.896051   
50                            Edogawabashi Station  35.709522  139.733581   
51                               Eifuku

In [41]:
#create a map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=10)

#set color scheme for the clusters
x=np.arange(kclusters+1)
ys=[i+x+(i*x)**2 for i in range(kclusters+1)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

#create a map
for lat, lon, poi, cluster in zip(tokyo_merged['latitude'], tokyo_merged['longitude'], tokyo_merged['station'], tokyo_merged['Cluster Label']):
    label = folium.Popup(str(poi) + 'Cluster' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7
    ).add_to(map_clusters)
    
map_clusters

<h2>Chapter 4: Conclusion and Observation</h2>

<h3>Cluster Label 0</h3>

<h3>These areas have convenience stores and restaurants</h3>

In [42]:
tokyo_merged.loc[tokyo_merged['Cluster Label'] ==0, tokyo_merged.columns[[0] + list(range(3, tokyo_merged.shape[1]))]]

station  total number of venues  \
2                   Akabane Station                   100.0   
7              Akebonobashi Station                    78.0   
12            Anamori-inari Station                    51.0   
15           Aomono-yokochō Station                    49.0   
23           Ariake Station (Tokyo)                    81.0   
27                Asukayama Station                    47.0   
29                    Ayase Station                    62.0   
31          Bakuro-yokoyama Station                   100.0   
32                Bakurochō Station                    89.0   
36      Chikatetsu-Narimasu Station                    63.0   
38       Chitose-karasuyama Station                    70.0   
93                 Hatagaya Station                    89.0   
120          Higashi-Nakano Station                    57.0   
121      Higashi-nihombashi Station                    80.0   
129                Hikifune Station                    43.0   
145                Ichigaya Station                    60.0   
155                Inarichō Station                    44.0   
158           Iriya Station (Tokyo)                    57.0   
168            Jūjō Station (Tokyo)                    55.0   
174                 Kameari Station                    78.0   
175                 Kameido Station                    67.0   
185               Kanamachi Station                    42.0   
186               Kanamechō Station                    44.0   
192          Kasuga Station (Tokyo)                   100.0   
193    Kasumigaseki Station (Tokyo)                   100.0   
197           Keikyū Kamata Station                    73.0   
203         Keisei Hikifune Station                    46.0   
204        Keisei Kanamachi Station                    43.0   
221              Kita-Senju Station                   100.0   
229              Kodemmachō Station                   100.0   
233                   Koiwa Station                    59.0   
236       Kokkai-gijidō-mae Station                    80.0   
240         Kokusai-Tenjijō Station                    80.0   
241  Kokusai-tenjijō-seimon Station                   100.0   
245        Komazawa-daigaku Station                    50.0   
263                 Kuramae Station                    82.0   
265                   Kyōdō Station                    69.0   
303          Monzen-Nakachō Station                   100.0   
309         Musashi-Koganei Station                    73.0   
334                Nakanobu Station                    44.0   
335                Narimasu Station                    70.0   
362            Nishi-waseda Station                    82.0   
374          Ochiai Station (Tokyo)                    62.0   
381                 Ogikubo Station                   100.0   
386             Ōji Station (Tokyo)                    51.0   
387              Ōji-ekimae Station                    51.0   
397            Omokagebashi Station                    57.0   
398           Ōmori Station (Tokyo)                   100.0   
403                Onarimon Station                   100.0   
405                Ōokayama Station                    60.0   
407                 Oshiage Station                    85.0   
421                 Ryōgoku Station                    85.0   
433                Sasazuka Station                    85.0   
446                 Sengawa Station                    63.0   
465               Shimbamba Station                    60.0   
482             Shin-koenji Station                    45.0   
484              Shin-Koiwa Station                    49.0   
486             Shin-Nakano Station                    41.0   
518           Sugamoshinden Station                    64.0   
529        Tachikawa-Minami Station                   100.0   
541             Takenotsuka Station                    58.0   
553           Tameike-Sannō Station                   100.0   
554                 Tanashi Station                    46.0

<h3>Cluster Label 1: These areas have many Japanese restaurants</h3>

In [43]:
tokyo_merged.loc[tokyo_merged['Cluster Label'] ==1, tokyo_merged.columns[[0] + list(range(3, tokyo_merged.shape[1]))]]

station  total number of venues  \
4              Akabanebashi Station                    55.0   
5         Akado-shōgakkōmae Station                    22.0   
11           Akitsu Station (Tokyo)                    58.0   
16                     Aoto Station                    33.0   
18          Araiyakushi-mae Station                    28.0   
19         Arakawa-itchūmae Station                    36.0   
20        Arakawa-nanachōme Station                    40.0   
22         Arakawa-shakomae Station                    31.0   
26             Asakusabashi Station                    49.0   
33              Bubaigawara Station                    53.0   
34               Chidorichō Station                    19.0   
35      Chikatetsu-Akatsuka Station                    40.0   
37        Chitose-Funabashi Station                    44.0   
44                Daishimae Station                    18.0   
45               Daitabashi Station                    40.0   
47           Ebara-Nakanobu Station                    46.0   
50             Edogawabashi Station                    56.0   
51                Eifukuchō Station                    25.0   
52                    Ekoda Station                    44.0   
55                     Fuda Station                    23.0   
56                 Fudō-mae Station                    30.0   
57                Fujimidai Station                    31.0   
59                 Funabori Station                    51.0   
69                 Gokokuji Station                    27.0   
72                 Gōtokuji Station                    29.0   
73             Hachimanyama Station                    49.0   
77                  Haijima Station                    22.0   
79          Hakusan Station (Tokyo)                    41.0   
81               Hamadayama Station                    40.0   
84             Hana-Koganei Station                    28.0   
91                   Hasune Station                    24.0   
92                 Hasunuma Station                    28.0   
94                Hatanodai Station                    49.0   
97                 Hatsudai Station                    60.0   
99         Heiwadai Station (Tokyo)                    32.0   
100               Heiwajima Station                    37.0   
101     Hibarigaoka Station (Tokyo)                    37.0   
106         Higashi-Fushimi Station                    19.0   
111            Higashi-Jūjō Station                    42.0   
112        Higashi-Kitazawa Station                    35.0   
113          Higashi-Kōenji Station                    47.0   
114         Higashi-Koganei Station                    44.0   
115          Higashi-Kurume Station                    31.0   
116       Higashi-matsubara Station                    35.0   
117        Higashi-Murayama Station                    30.0   
118        Higashi-Nagasaki Station                    28.0   
122    Higashi-ogu-sanchōme Station                    34.0   
125        Higashi-Shinjuku Station                    73.0   
126        Higashi-Mukōjima Station                    24.0   
131            Hino Station (Tokyo)                    40.0   
133           Hirai Station (Tokyo)                    47.0   
138            Hon-komagome Station                    33.0   
139                Hōnanchō Station                    36.0   
140          Hongō-sanchōme Station                    38.0   
141        Honjo-azumabashi Station                    40.0   
143         Horikirishōbuen Station                    30.0   
144                    Hōya Station                    34.0   
146                 Ichinoe Station                    37.0   
149                 Ikegami Station                    43.0   
150          Ikejiri-Ōhashi Station                    42.0   
154          Inagi-Naganuma Station                    18.0   
161                Itabashi Station                    42.0   
162          Itabashihoncho Station                    31.0

<h3>Cluster Label 2: These areas have convenience stores and restaurants, and the total numbers of venues are mostly less than 50.</h3>

In [44]:
tokyo_merged.loc[tokyo_merged['Cluster Label'] ==2, tokyo_merged.columns[[0] + list(range(3, tokyo_merged.shape[1]))]]

station  total number of venues  \
3       Akabane-iwabuchi Station                    61.0   
9              Akihabara Station                   100.0   
28              Awajichō Station                   100.0   
70               Gotanda Station                   100.0   
148            Ikebukuro Station                   100.0   
163           Iwamotocho Station                   100.0   
173       Kamata Station (Tokyo)                    72.0   
187        Kanda Station (Tokyo)                   100.0   
208          Keisei Ueno Station                   100.0   
213            Kinshichō Station                   100.0   
230               Kōenji Station                   100.0   
325     Naka-Okachimachi Station                   100.0   
384              Ōimachi Station                    92.0   
390          Okachimachi Station                   100.0   
436       Seibu-Shinjuku Station                   100.0   
466            Shimbashi Station                   100.0   
502  Shinjuku-Nishiguchi Station                   100.0   
503    Shinjuku-sanchōme Station                   100.0   
506              Shinsen Station                   100.0   
508             Shiodome Station                    72.0   
519           Suidōbashi Station                   100.0   
530         Takadanobaba Station                    84.0   
590        Uchisaiwaicho Station                   100.0   
591                 Ueno Station                   100.0   
592        Ueno-hirokoji Station                   100.0   
593     Ueno-okachimachi Station                   100.0   
618     Yotsuya-sanchōme Station                    71.0   
625      Yushima Station (Tokyo)                   100.0   

    1st Most Common Venue      2nd Most Common Venue 3rd Most Common Venue  \
3                Sake Bar          Convenience Store      Ramen Restaurant   
9       Electronics Store                 Hobby Shop              Sake Bar   
28       Ramen Restaurant  Japanese Curry Restaurant                  Café   
70               Sake Bar        Japanese Restaurant      Ramen Restaurant   
148              Sake Bar           Ramen Restaurant                  Café   
163              Sake Bar           Ramen Restaurant   Japanese Restaurant   
173      Ramen Restaurant                   Sake Bar   Japanese Restaurant   
187              Sake Bar                 Hobby Shop      Ramen Restaurant   
208              Sake Bar                  BBQ Joint   Japanese Restaurant   
213      Ramen Restaurant                   Sake Bar           Coffee Shop   
230              Sake Bar           Ramen Restaurant                  Café   
325              Sake Bar                  BBQ Joint      Ramen Restaurant   
384      Ramen Restaurant        Japanese Restaurant     Convenience Store   
390              Sake Bar                  BBQ Joint      Ramen Restaurant   
436      Ramen Restaurant                   Sake Bar             BBQ Joint   
466              Sake Bar        Japanese Restaurant    Seafood Restaurant   
502              Sake Bar           Ramen Restaurant                  Café   
503                   Bar                  BBQ Joint              Sake Bar   
506   Japanese Restaurant                   Sake Bar             Nightclub   
508              Sake Bar         Seafood Restaurant             BBQ Joint   
519      Ramen Restaurant                 Steakhouse                 Hotel   
530      Ramen Restaurant                   Sake Bar   Tonkatsu Restaurant   
590              Sake Bar        Japanese Restaurant             BBQ Joint   
591              Sake Bar        Japanese Restaurant      Ramen Restaurant   
592              Sake Bar                  BBQ Joint      Ramen Restaurant   
593              Sake Bar                  BBQ Joint      Ramen Restaurant   
618              Sake Bar           Ramen Restaurant     Convenience Store   
625      Ramen Restaurant                   Sake Bar                  Café   

    4th Most Common V

<h3>Cluster Label 3: These areas have many sake bars. These seem to be drinking places.</h3>

In [45]:
tokyo_merged.loc[tokyo_merged['Cluster Label'] ==3, tokyo_merged.columns[[0] + list(range(3, tokyo_merged.shape[1]))]]

station  total number of venues  \
0                              Adachi-Odai Station                     8.0   
1                                   Aihara Station                    16.0   
8                                  Akigawa Station                    11.0   
10                                Akishima Station                    12.0   
13                                     Aoi Station                    19.0   
14                                    Aomi Station                    41.0   
21                         Arakawa-nichōme Station                    20.0   
24                   Ariake-tennis-no-mori Station                    13.0   
39                           Chōfu Station (Tokyo)                    31.0   
40             Chūō-Daigaku-Meisei-Daigaku Station                    12.0   
46                            Den-en-chōfu Station                    31.0   
49                                 Edogawa Station                    19.0   
53                               Etchūjima Station                    31.0   
54                           Fuchū Station (Tokyo)                     6.0   
58                             Fujimigaoka Station                    21.0   
60                       Fune-no-kagakukan Station                    36.0   
61                                   Fussa Station                    17.0   
63                               Futamatao Station                     5.0   
64                                Gaiemmae Station                    50.0   
65                         Gakugei-daigaku Station                    45.0   
66                          Gakushuinshita Station                    18.0   
71                                 Gotanno Station                    25.0   
74                                Hachiōji Station                     9.0   
75                       Hachiōji-Minamino Station                    31.0   
76                                Hagiyama Station                     9.0   
78                            Hakonegasaki Station                    14.0   
80                                 Hamacho Station                    37.0   
83                                  Hamura Station                     9.0   
86   Haneda Airport International Terminal Station                    51.0   
88               Haneda Airport Terminal 2 Station                    63.0   
95                      Hatchōbori Station (Tokyo)                    50.0   
96                                Hatonosu Station                    10.0   
98                          Hazama Station (Tokyo)                    48.0   
103                          Higashi-Akiru Station                     6.0   
104                          Higashi-Azuma Station                    13.0   
105                          Higashi-fuchū Station                    29.0   
107                          Higashi-Fussa Station                    22.0   
109                      Higashi-Ikebukuro Station                    34.0   
110             Higashi-ikebukuro-yonchome Station                    29.0   
119                       Higashi-Nakagami Station                    20.0   
123                          Higashi-ojima Station                    25.0   
124                            Higashi-Ōme Station                    18.0   
127                            Hikarigaoka Station                    47.0   
128                              Hikawadai Station                    15.0   
130                             Hinatawada Station                     5.0   
134                     Hirayamajōshi-kōen Station                     5.0   
136                    Hitotsubashi-Gakuen Station                    10.0   
137                               Hodokubo Station                     4.0   
142                               Horikiri Station                    19.0   
147                              Iidabashi Station                    62.0   
151                                Ikenoue Station               

<h3>Cluster Label 4: These areas have mostly less than 20 venues. These areas seem to be suburb areas.</h3>

In [46]:
tokyo_merged.loc[tokyo_merged['Cluster Label'] ==4, tokyo_merged.columns[[0] + list(range(3, tokyo_merged.shape[1]))]]

station  total number of venues  \
6                     Akasaka-mitsuke Station                    86.0   
17                     Aoyama-itchōme Station                    70.0   
25                            Asagaya Station                    60.0   
30                        Azabu-juban Station                   100.0   
41                      Daiba Station (Tokyo)                   100.0   
42                        Daikan-yama Station                   100.0   
43                     Daimon Station (Tokyo)                    79.0   
48                      Ebisu Station (Tokyo)                   100.0   
62                    Futako-Tamagawa Station                   100.0   
67                              Ginza Station                   100.0   
68                      Ginza-itchōme Station                   100.0   
82                       Hamamatsuchō Station                   100.0   
85   Haneda Airport Domestic Terminal Station                    69.0   
87          Haneda Airport Terminal 1 Station                    67.0   
89                           Hanzōmon Station                    79.0   
90                           Harajuku Station                   100.0   
102                            Hibiya Station                   100.0   
108                     Higashi-ginza Station                   100.0   
135                             Hiroo Station                    93.0   
166                          Jimbōchō Station                   100.0   
167                 Jiyūgaoka Station (Tokyo)                    95.0   
171                        Kagurazaka Station                    96.0   
196                         Kayabachō Station                    75.0   
211                         Kichijōji Station                   100.0   
234                         Kōjimachi Station                    79.0   
247                          Kōrakuen Station                   100.0   
255                        Kudanshita Station                    61.0   
264                  Kyōbashi Station (Tokyo)                   100.0   
272                       Manseibashi Station                   100.0   
277                    Meiji-jingumae Station                   100.0   
286                   Minami-Shinjuku Station                   100.0   
293                              Mita Station                    61.0   
297                     Mitsukoshimae Station                   100.0   
306                          Mukōhara Station                    48.0   
324                       Naka-Meguro Station                   100.0   
341                        Nihombashi Station                   100.0   
342                      Nijūbashimae Station                   100.0   
343                         Ningyōchō Station                   100.0   
353                     Nishi-Ogikubo Station                   100.0   
356                    Nishi-Shinjuku Station                   100.0   
360                    Nishi-Taishidō Station                    93.0   
370                          Nogizaka Station                   100.0   
373                        Ochanomizu Station                    85.0   
379                Ogawamachi Station (Tokyo)                   100.0   
401                        Omotesandō Station                   100.0   
408                  Ōtemachi Station (Tokyo)                   100.0   
419                          Roppongi Station                   100.0   
420                  Roppongi-itchōme Station                   100.0   
431                       Sangen-Jaya Station                   100.0   
444                           Sendagi Station                    53.0   
456                         Shibakoen Station                    75.0   
461                           Shibuya Station                   100.0   
471                    Shimo-kitazawa Station                   100.0   
487                   Shin-Nihombashi Station                   100.0   
488                   S

<h3>Cluster Label 5:These areas have cafe and shopping places. These areas seem to be shopping places in central Tokyo.</h3>

In [47]:
tokyo_merged.loc[tokyo_merged['Cluster Label'] ==5, tokyo_merged.columns[[0] + list(range(3, tokyo_merged.shape[1]))]]

station  total number of venues 1st Most Common Venue  \
132      Hinode Station                     NaN                   NaN   
190       Kasai Station                     NaN                   NaN   
249        Kori Station                     NaN                   NaN   
252      Kosuge Station                     NaN                   NaN   
326    Nakagami Station                     NaN                   NaN   
393     Okusawa Station                     NaN                   NaN   
434       Sawai Station                     NaN                   NaN   
547  Tama-reien Station                     NaN                   NaN   
609        Yaho Station                     NaN                   NaN   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
132                   NaN                   NaN                   NaN   
190                   NaN                   NaN                   NaN   
249                   NaN                   NaN                   NaN   
252                   NaN                   NaN                   NaN   
326                   NaN                   NaN                   NaN   
393                   NaN                   NaN                   NaN   
434                   NaN                   NaN                   NaN   
547                   NaN                   NaN                   NaN   
609                   NaN                   NaN                   NaN   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
132                   NaN                   NaN                   NaN   
190                   NaN                   NaN                   NaN   
249                   NaN                   NaN                   NaN   
252                   NaN                   NaN                   NaN   
326                   NaN                   NaN                   NaN   
393                   NaN                   NaN                   NaN   
434                   NaN                   NaN                   NaN   
547                   NaN                   NaN                   NaN   
609                   NaN                   NaN                   NaN   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  \
132                   NaN                   NaN                    NaN   
190                   NaN                   NaN                    NaN   
249                   NaN                   NaN                    NaN   
252                   NaN                   NaN                    NaN   
326                   NaN                   NaN                    NaN   
393                   NaN                   NaN                    NaN   
434                   NaN                   NaN                    NaN   
547                   NaN                   NaN                    NaN   
609                   NaN                   NaN                    NaN   

     Cluster Label  
132              5  
190              5  
249              5  
252              5  
326              5  
393              5  
434              5  
547              5  
609              5

In [34]:
tokyo_merged.loc[tokyo_merged['Cluster Label'] ==6, tokyo_merged.columns[[0] + list(range(3, tokyo_merged.shape[1]))]]

station  total number of venues 1st Most Common Venue  \
132      Hinode Station                     NaN                   NaN   
190       Kasai Station                     NaN                   NaN   
249        Kori Station                     NaN                   NaN   
252      Kosuge Station                     NaN                   NaN   
326    Nakagami Station                     NaN                   NaN   
393     Okusawa Station                     NaN                   NaN   
434       Sawai Station                     NaN                   NaN   
547  Tama-reien Station                     NaN                   NaN   
609        Yaho Station                     NaN                   NaN   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
132                   NaN                   NaN                   NaN   
190                   NaN                   NaN                   NaN   
249                   NaN                   NaN                   NaN   
252                   NaN                   NaN                   NaN   
326                   NaN                   NaN                   NaN   
393                   NaN                   NaN                   NaN   
434                   NaN                   NaN                   NaN   
547                   NaN                   NaN                   NaN   
609                   NaN                   NaN                   NaN   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
132                   NaN                   NaN                   NaN   
190                   NaN                   NaN                   NaN   
249                   NaN                   NaN                   NaN   
252                   NaN                   NaN                   NaN   
326                   NaN                   NaN                   NaN   
393                   NaN                   NaN                   NaN   
434                   NaN                   NaN                   NaN   
547                   NaN                   NaN                   NaN   
609                   NaN                   NaN                   NaN   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  \
132                   NaN                   NaN                    NaN   
190                   NaN                   NaN                    NaN   
249                   NaN                   NaN                    NaN   
252                   NaN                   NaN                    NaN   
326                   NaN                   NaN                    NaN   
393                   NaN                   NaN                    NaN   
434                   NaN                   NaN                    NaN   
547                   NaN                   NaN                    NaN   
609                   NaN                   NaN                    NaN   

     Cluster Label  
132              6  
190              6  
249              6  
252              6  
326              6  
393              6  
434              6  
547              6  
609              6